In [1]:
from IPython.display import display
from matplotlib.ticker import StrMethodFormatter
from matplotlib.ticker import FormatStrFormatter

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import pickle
import re
import spacy

pd.options.display.max_columns = None
pd.options.display.max_rows = None
pd.set_option('display.max_colwidth', None)

%matplotlib inline


In [ ]:
# dir = "/home/mikes/Documents/jupyterEnvironments/VAERS_analysis/"
# file = "VAERS data deaths only Edited for NLP.csv"
# #file = "VAERS data deaths only Edited for NLP for HAD COVID.csv"
# path = os.path.join(dir, file)

# vd = pd.read_csv(path, 
#                  delimiter = ",", 
#                  encoding = "ISO-8859-1")
# vd.columns

In [2]:
vd = pd.read_csv("/home/mikes/Windows/Documents/tmp/VAERS data deaths only for NLP in Hospice or was terminal.csv", 
                         delimiter = ",", 
                         encoding = "ISO-8859-1")

# vd = pd.read_csv("./VAERS data deaths only Edited for NLP for HAD COVID.csv", 
#                          delimiter = ",", 
#                          encoding = "ISO-8859-1")

# Prune all rows from previous search of covid positive to avoid overlaps
covid_pos_VAERS_IDs = pickle.load( open( "./VAERS_IDs.pickle", "rb" ) )
print("before...", vd.shape)
vd = vd[~vd['VAERS_ID'].isin(covid_pos_VAERS_IDs)]
print("after...", vd.shape)

# Concatenate the pertinent columns
def concat_columns(row):
    result = ''.join(["(VAX_DATE)", str(row["VAX_DATE"]),
                             "(SYMPTOM_TEXT)", row["SYMPTOM_TEXT"], 
                             "(LAB_DATA)", row["LAB_DATA"], 
                             "(CUR_ILL)", row["CUR_ILL"], 
                             "(HISTORY)", row["HISTORY"] ])
vd["CONCAT_TEXT"] = vd.apply(
      lambda row:
        ''.join(["(VAX_DATE)",     str(row["VAX_DATE"]).lower(),
                 " (SYMPTOM_TEXT)", str(row["SYMPTOM_TEXT"]).lower(), 
                 " (LAB_DATA)",     str(row["LAB_DATA"]).lower(), 
                 " (CUR_ILL)",      str(row["CUR_ILL"]).lower(), 
                 " (HISTORY)",      str(row["HISTORY"]) ]).lower(),
      axis=1
  )
vd.columns
display(vd.head())

before... (5184, 36)
after... (4789, 36)


VAERS_ID  HOSPICE_TARGET  RECVDATE STATE  AGE_YRS  CAGE_YR  CAGE_MO SEX  \
0    916803             NaN  1/1/2021    LA     78.0     78.0      NaN   M   
4    918065             NaN  1/4/2021    CA     64.0     64.0      NaN   M   
5    918388             NaN  1/4/2021    FL     65.0     65.0      NaN   F   
6    918418             1.0  1/4/2021    FL     65.0     65.0      NaN   M   
7    918487             NaN  1/4/2021    MI     94.0     93.0      NaN   M   

  RPT_DATE  \
0      NaN   
4      NaN   
5      NaN   
6      NaN   
7      NaN   

                                                                                                                                                                                                                                                                           SYMPTOM_TEXT  \
0                                                                                                                                                                                                                                                                      respitory colase   
4                                                                                                                                                                                                             1/1/2020: Residents was found unresponsive. Pronounced deceased at 6:02pm   
5                                                                                                                                                                            Resident found unresponsive without pulse, respirations at 04:30 CPR performed, expired at 04:52 by Rescue   
6  Resident became SOB, congested and hypoxic requiring oxygen, respiratory treatments and suctioning.  Stabilized after treatment and for the next 72 hours with oxygen saturations in the 90s.  On 1/3/2021 was found without pulse and respirations.  Resident was a DNR on Hospice.   
7                                                                                                                                                                                                               Two days post vaccine patient went into cardiac arrest and passed away.   

  DIED    DATEDIED L_THREAT  ER_VISIT HOSPITAL  HOSPDAYS X_STAY DISABLE  \
0    Y  10/18/2020        Y       NaN        Y       8.0    NaN     NaN   
4    Y    1/1/2021      NaN       NaN      NaN       NaN    NaN     NaN   
5    Y    1/1/2021      NaN       NaN      NaN       NaN    NaN     NaN   
6    Y    1/3/2021      NaN       NaN      NaN       NaN    NaN     NaN   
7    Y    1/4/2021      NaN       NaN      NaN       NaN    NaN     NaN   

  RECOVD    VAX_DATE  ONSET_DATE  NUMDAYS  \
0      N   10/6/2020  10/10/2020      4.0   
4      N  12/30/2020    1/1/2021      2.0   
5      N  12/30/2020    1/1/2021      2.0   
6      N  12/30/2020    1/1/2021      2.0   
7      N    1/2/2020    1/4/2021    368.0   

                                       LAB_DATA V_ADMINBY V_FUNDBY  \
0  Hospitalized 10/11/2020  and died 11/18/2020       PVT      NaN   
4                                           NaN       OTH      NaN   
5                                           NaN       SEN      NaN   
6                         low oxygen saturation       SEN      NaN   
7                                          None       SEN      NaN   

                                                                                                                                                                                                            OTHER_MEDS  \
0                                                           Lisinopril, Novolog,, Lantus Solostar, Gabapentin, Glusosamine-chondrotin, Lanaoprost, Alphagan, Metoprol Tartrate,  Colocrys. . as needed, Chlorthlidone.   
4                                 - Invega Trenza 546mg Q3months  - Lithium 300mg BID - Oxybutynin 5mg QID - lipitor 20mg QHS  - cogentin 2mg BID  - Norvasc 5mg QD - Dyazi

In [3]:
p = ''.join([".*Hospice\s*re[cs].*", "|", 
             ".*[io]n\s*hospice.*", "|",
             ".*under\s*hospice\s*care.*"
            ])

df_CONCAT_TEXT = vd[vd['CONCAT_TEXT'].str.lower().str.count(p)>0]
print(df_CONCAT_TEXT.shape)

# df_LAB_DATA = vd[vd['LAB_DATA'].str.lower().str.count('^.*[oi]n hospice.*$')>0]
# print(df_LAB_DATA.shape)

# df_HISTORY = vd[vd['HISTORY'].str.lower().str.count('^.*hospice.*$')>0]
# print(df_HISTORY.shape)

# df_CUR_ILL = vd[vd['CUR_ILL'].str.lower().str.count('^.*hospice.*$')>0]
# print(df_CUR_ILL.shape)

(146, 37)


In [ ]:
# This was used to search for regex phrases from this specific dataset
p = "((?:^|\w+\s+\w+\s+\w+\s+)hospice(?:\s+\w+\s+\w+\s+\w+|$))"
l = vd['CONCAT_TEXT'].str.extract(p).dropna()[0].tolist()
s = set(l)

# (transferred|admitted|entered hospice [on]* <date>
positives = ["[io]n\s*hospice",
             "under\s*hospice",             
             "hospice\s*[a-z0-9]*\sprior", 
             "hospice\s*patient",
             "receiv(e|ed|ing)\s*(home)?\s*hospice",
             "hospice\s*recipient",
             "history\s*included\s*[\w\s]+hospice", 
             "discharged\s*from\s*hospice"
             "had\s*been\s[\s\w\s]*hospice",
             
            ]
for phrase in positives: 
    s = [i for i in s if not re.search(phrase, i)]

negatives = ["transition(ed|ing)* to hospice", 
             "moved to hospice", 
            "hospice was called in", 
             "discharg(e|ed|ing)*\s*(on|to|into)\s*hospice", 
             "hospice\s*referral"
            ]    
for phrase in negatives: 
    s = [i for i in s if not re.search(phrase, i)]

print("({}){}".format(len(s), s))

In [4]:

p = "[io]n\s*hospice|under\s*hospice|hospice\s*[a-z0-9]*\sprior|hospice\s*patient|receiv(e|ed|ing)\s*(home)?\s*hospice|hospice\s*recipient|history\s*included\s*[\w\s]+hospice|discharged\s*from\s*hospice|had\s*been\s[\s\w\s]*hospice"
df = vd[vd['CONCAT_TEXT'].str.lower().str.count(p)>0]
print(df.shape)
p = "transition(ed|ing)*\s*(to|in|into)*\s*hospice|mov(e|ed|ing)?\s*(to|in|into)*\s*hospice|hospice\s*was\s*called\s*in|discharg(e|ed|ing)*\s*(on|to|into)\s*(home)?\s*hospice|hospice\s*refer(red|ral)?"
notdf = vd[vd['CONCAT_TEXT'].str.lower().str.count(p)>0]
print(notdf.shape)
df = df[~df['VAERS_ID'].isin(notdf['VAERS_ID'].tolist())]
print(df.shape)
display(df)

(189, 37)
(29, 37)
(185, 37)


VAERS_ID  HOSPICE_TARGET   RECVDATE STATE  AGE_YRS  CAGE_YR  CAGE_MO  \
6       918418             1.0   1/4/2021    FL     65.0     65.0      NaN   
12      920326             1.0   1/5/2021    IN     89.0     89.0      NaN   
18      921481             1.0   1/5/2021    OH     88.0     88.0      NaN   
23      921880             1.0   1/5/2021    VA     96.0     96.0      NaN   
44      928513             1.0   1/8/2021    MI     72.0     72.0      NaN   
46      929359             1.0   1/8/2021    FL     76.0     76.0      NaN   
48      929997             1.0   1/8/2021    WI     86.0     86.0      NaN   
60      956966             1.0   1/9/2021   NaN     86.0     85.0      NaN   
61      964629             1.0   1/9/2021   NaN     64.0     63.0      NaN   
62      964636             1.0   1/9/2021   NaN     81.0     80.0      NaN   
105     940855             1.0  1/13/2021    AR     79.0     79.0      NaN   
109     941561             1.0  1/13/2021    MN     91.0     91.0      NaN   
110     941607             1.0  1/13/2021    IN     83.0     83.0      NaN   
122     943442             1.0  1/14/2021    GA     68.0     68.0      NaN   
126     944439             1.0  1/14/2021    KY     62.0     62.0      NaN   
157     949630             1.0  1/15/2021    HI     98.0     98.0      NaN   
224     959147             1.0  1/20/2021    OH     84.0     83.0      NaN   
228     959272             1.0  1/20/2021    KS     85.0     85.0      NaN   
242     960552             1.0  1/21/2021   NaN     78.0     78.0      NaN   
254     962308             1.0  1/21/2021    UT      NaN      NaN      NaN   
285     965565             1.0  1/22/2021    NE     84.0     84.0      NaN   
311     969648             NaN  1/25/2021   NaN      NaN      NaN      NaN   
326     971736             NaN  1/25/2021    IA     88.0     88.0      NaN   
330     972113             0.0  1/25/2021    TN     91.0     91.0      NaN   
338     972782             1.0  1/25/2021    CA     81.0     81.0      NaN   
383     977426             1.0  1/27/2021    GA     70.0     70.0      NaN   
406     979926             1.0  1/27/2021    CA     81.0     81.0      NaN   
412     983721             1.0  1/27/2021   NaN     72.0     71.0      NaN   
422     982218             1.0  1/28/2021    MO     63.0     63.0      NaN   
453     985715             NaN  1/29/2021    FL     80.0     80.0      NaN   
455     985933             NaN  1/29/2021   NaN      NaN      NaN      NaN   
456     986063             1.0  1/29/2021    UT     83.0     83.0      NaN   
477     987877             1.0  1/30/2021    MI     86.0     86.0      NaN   
484     990780             1.0   2/1/2021    MI     75.0     75.0      NaN   
493     991859             1.0   2/1/2021    IL     89.0     89.0      NaN   
499     992154             1.0   2/1/2021    MN    100.0    100.0      NaN   
516     995147             0.0   2/1/2021   NaN     88.0     86.0      NaN   
542     996105             1.0   2/2/2021    CA     95.0     95.0      NaN   
595    1002636             0.0   2/4/2021    WA     90.0     90.0      NaN   
599    1003106             1.0   2/4/2021    CA     92.0     92.0      NaN   
607    1004206             1.0   2/5/2021    MN     91.0     91.0      NaN   
673    1011905             1.0   2/8/2021    NH     91.0     91.0      NaN   
714    1016709             1.0   2/9/2021    MN     93.0     93.0      NaN   
796    1024592             1.0  2/11/2021    CA     80.0     80.0      NaN   
856    1029003             1.0  2/14/2021    FL     82.0     82.0      NaN   
887    1031629             0.0  2/15/2021    IA     85.0     85.0      NaN   
905    1032880             1.0  2/16/2021    KY     78.0     78.0      NaN   
922    1034182             0.0  2/16/2021    CO     82.0     82.0      NaN   
952    1036440             NaN  2/17/2021    GA     65.0     65.0      NaN   
967    1036748             1.0  2/17/2021    IL     83.0     83.0      NaN   
986    1038234             0

In [5]:
# Methods:
The VAERS data was downloaded for all of 2021, first week of July from https://vaers.hhs.gov/data.html. Data was filtered to include only rows where column "DIED" == "Y".

Two columns were pertinent to the disucsion: "SYMPTOM_TEXT" and "LAB_DATA". Information verifying that patient had covid may appear in one or both columns, so each column was processed separately. The results of each search were then concatenated together, and duspliactes were removed based on "VAERS_ID". The row counts were then tallied.  

The model was trained by manually adding the columns: "SYMPTOM_TEXT_TARGET" and "LAB_DATA_TARGET". These columns were manually marked with a 0 (not infected with covid) or 1 (infected with covid) based on the contents of the "SYMPTOM_TEXT" and "LAB_DATA" columns (respectively.) A pateint was considered "Infected with covid" if they had a positive test within 30 days prior to the vaccination, after shot, or if the text annotated that the patient ad covid symptoms or died of a covid related symptom.

The model was trained the dataset using Logistic Regression(tf-idf), and then ran the model against the entire death-only VAERS data, including the data from the training set (in order to capture the total of all patients who had, developed, or died of covid.)

101 positive (1s) and 101 negative (0s) were marked for SYMPTOM_TEXT_TARGET
105 positive (1s) and 104 negative (0s) were marked for LAB_DATA_TARGET

From a randomly selected run from "SYMPTOM TEXT", 12 out of 233 were incorrect (0.0482)
Assuming a 5% error rate when using .80 from the "predict_prob" column as the cutoff 


# Results:
Out of 5184 reports of deaths after vaccination ...<br>

**Average number of covid positives in VAERS data (deaths only):  240.06499999999997**

**Average percent of covid positives in VAERS data (deaths only):  4.63088348765432**




SyntaxError: invalid syntax (<ipython-input-5-45cceb31092a>, line 2)

In [1]:
# This was used to search for regex phrases from this specific dataset
p = "((?:^|(\w+\s+){1,6})terminal(?:(\s+\w+){1,6}|$))"
#p = "(.* terminal .*)"

l = vd['CONCAT_TEXT'].str.extract(p).dropna()[0].tolist()
#s = set(l)

for i in l: 
    print(); print(i)
# After manually looking at all returns, selected the negatives by hand. The remaining results were positives, and were added to the df_TERMINAL df
# # (transferred|admitted|entered hospice [on]* <date>
# positives = [
             
#             ]
# for phrase in positives: 
#     s = [i for i in s if not re.search(phrase, i)]

# negatives = [
    
#             ]    
# for phrase in negatives: 
#     s = [i for i in s if not re.search(phrase, i)]

# print("({}){}".format(len(s), s))

NameError: name 'vd' is not defined